### Bibliotecas

In [19]:
# Bibliotecas
import meteomatics.api as api
import datetime as dt
import os
import numpy as np
import geopandas as gpd
from shapely.wkt import loads
from shapely.geometry import Polygon
import pandas as pd
import cx_Oracle
import logging
from funcoes_conexao import conexao_oracle, finaliza_conexao, consulta_para_dataframe, truncate_tabelas
from dotenv import load_dotenv
load_dotenv()

True

In [20]:
# Configurar o logging
logging.basicConfig(level=logging.INFO, format='%(asctime)s - %(levelname)s - %(message)s')

### Diretórios

In [21]:
BASE_DIR = os.getcwd()
DIR_PAI = os.path.dirname(os.path.dirname(BASE_DIR))
DIR_COLETA_DADOS = os.path.join(DIR_PAI, "Coleta de Dados")

In [22]:
# Carregar dados login Oracle
username_ocr = os.getenv('USERNAME_ORC')
password_ocr = os.getenv("PASSWORD_ORC")
dsn = 'ORACLE.FIAP.COM.BR:1521/ORCL'

In [23]:
# Carregar dados login Weather
username = os.getenv('USERNAME_WEATHER_API')
password = os.getenv('PASSWORD_WEATHER_API')

#### Inicializando Conexão ORC

In [24]:
connection, cursor = conexao_oracle(username_ocr, password_ocr, dsn)

#if connection and cursor:
#    finaliza_conexao(cursor, connection)

(1, 'Centro Ampliado', <cx_Oracle.Object MDSYS.SDO_GEOMETRY at 0x79e31c30>, <cx_Oracle.Object MDSYS.SDO_GEOMETRY at 0x79e31d10>)
(2, 'Zona Leste 1', <cx_Oracle.Object MDSYS.SDO_GEOMETRY at 0x79e31d70>, <cx_Oracle.Object MDSYS.SDO_GEOMETRY at 0x79e31990>)
(3, 'Zona Leste 2', <cx_Oracle.Object MDSYS.SDO_GEOMETRY at 0x79e31c30>, <cx_Oracle.Object MDSYS.SDO_GEOMETRY at 0x79e31d10>)
(4, 'Zona Norte', <cx_Oracle.Object MDSYS.SDO_GEOMETRY at 0x79e31cf0>, <cx_Oracle.Object MDSYS.SDO_GEOMETRY at 0x79e31d70>)
(5, 'Zona Sul', <cx_Oracle.Object MDSYS.SDO_GEOMETRY at 0x79e31c30>, <cx_Oracle.Object MDSYS.SDO_GEOMETRY at 0x79e31d10>)


#### Limpa Tabelas

In [25]:
#truncate_tabelas(connection, 'TBL_Previsao_Futura')

#### INSERT COORDENADAS - tb_clima_prev

##### Cosulta região banco de dados

In [26]:
def read_zona_data(connection):
    cursor = connection.cursor()
    
    try:
        # Consultar dados da tabela TBL_ZONA
        cursor.execute("""
            SELECT 
                CD_ZONA, 
                NM_ZONA, 
                SDO_UTIL.TO_WKTGEOMETRY(GEOMETRY) as geometry_wkt, 
                SDO_UTIL.TO_WKTGEOMETRY(COORD_CENTRAL) as coord_central_wkt 
            FROM TB_ZONA
        """)
        
        rows = cursor.fetchall()

        # Extrair as colunas dos resultados
        col_names = [desc[0] for desc in cursor.description]

        # Criar um DataFrame com os resultados
        df = pd.DataFrame(rows, columns=col_names)

        # Converter colunas LOB para string e remover as colunas extras
        df['geometry'] = df['GEOMETRY_WKT'].apply(lambda x: loads(x.read()) if isinstance(x, cx_Oracle.LOB) else loads(x))
        df['COORD_CENTRAL'] = df['COORD_CENTRAL_WKT'].apply(lambda x: loads(x.read()) if isinstance(x, cx_Oracle.LOB) else (loads(x) if x else None))

        # Remover colunas WKT que não são mais necessárias
        df.drop(columns=['GEOMETRY_WKT', 'COORD_CENTRAL_WKT'], inplace=True)

        # Criar um GeoDataFrame
        gdf = gpd.GeoDataFrame(df, geometry='geometry')

        return gdf

    except cx_Oracle.DatabaseError as e:
        error, = e.args
        print(f"Erro ao ler dados: {error.message}")

    finally:
        if cursor:
            cursor.close()
        print("Cursor fechado.")

In [27]:
# Ler os dados da tabela
Select_TBL_Zona = read_zona_data(connection)
Select_TBL_Zona

Cursor fechado.


CD_ZONA          NM_ZONA  \
0        1  Centro Ampliado   
1        2     Zona Leste 1   
2        3     Zona Leste 2   
3        4       Zona Norte   
4        5         Zona Sul   

                                            geometry  \
0  POLYGON ((-46.67421 -23.64222, -46.67437 -23.6...   
1  POLYGON ((-46.57536 -23.6008, -46.57552 -23.60...   
2  POLYGON ((-46.45643 -23.64132, -46.4565 -23.64...   
3  POLYGON ((-46.67805 -23.51367, -46.67863 -23.5...   
4  POLYGON ((-46.60925 -23.90462, -46.60876 -23.9...   

                   COORD_CENTRAL  
0  POINT (-46.679579 -23.582388)  
1  POINT (-46.542663 -23.561831)  
2  POINT (-46.443353 -23.549433)  
3   POINT (-46.673093 -23.45335)  
4  POINT (-46.708599 -23.813758)

In [28]:
Select_TBL_Zona.to_csv('Select_TBL_Zona.csv', index=False)

In [29]:
# Consulta SQL
query_teste = "SELECT * FROM tb_clima_prev"

# Executa a consulta e obtém os resultados em um DataFrame
df_teste = consulta_para_dataframe(cursor, query_teste)
df_teste

Empty DataFrame
Columns: [CD_PREVISAO, TB_ZONA_CD_ZONA, DT_REFERENCIA, DT_FUTURA, TEMP_MAX, TEMP_MIN, UMID_MAX, UMID_MIN, VEL_VENTO, VOL_PRECIPITACAO, TP_NUVEM, PRESSAO_ATM]
Index: []

##### Chamada API

In [30]:
# Parâmetros da API disponíveis na versão gratuita
parameters = {
    't_max_2m_24h:C': 'TEMP_MAX',
    't_min_2m_24h:C': 'TEMP_MIN',
    'relative_humidity_2m:p': 'UMID_MAX',
    'wind_gusts_10m_1h:ms': 'VEL_VENTO',
    'precip_24h:mm': 'VOL_PRECIPITACAO',
    'total_cloud_cover:octas': 'TP_NUVEM',
    'msl_pressure:hPa': 'PRESSAO_ATM'
}

model = 'mix'
startdate = dt.datetime.utcnow().replace(minute=0, second=0, microsecond=0)
enddate = startdate + dt.timedelta(days=7)
interval = dt.timedelta(hours=1)

In [31]:
# Dicionário para armazenar os dados de cada zona
dados_zonas = {}

In [32]:
for idx, row in Select_TBL_Zona.iterrows():
    zona_geom = loads(row['geometry']) if isinstance(row['geometry'], str) else row['geometry']
    zona_geom_simplificada = zona_geom.simplify(0.01, preserve_topology=True)
    
    coords = [(lat, lon) for lon, lat in zona_geom_simplificada.exterior.coords]
    coords_str = ','.join([f"{lat},{lon}" for lat, lon in coords])
    request_url = f'https://api.meteomatics.com/{startdate.strftime("%Y-%m-%dT%H:%M:%SZ")}/{"".join(parameters.keys())}/polygon({coords_str})/json?model={model}'
    
    print(f"URL de requisição para a zona {row['NM_ZONA']}: {request_url}")
    
    try:
        df = api.query_time_series(coords, startdate, enddate, interval, list(parameters.keys()), username, password, model=model)
        df.reset_index(inplace=True)
        df.rename(columns={'validdate': 'DATA_FUTURA'}, inplace=True)
        df.columns = [parameters.get(col, col) for col in df.columns]
        dados_zonas[row['NM_ZONA']] = df
    except Exception as e:
        logging.error(f"Erro ao processar a zona {row['NM_ZONA']}: {e}")

URL de requisição para a zona Centro Ampliado: https://api.meteomatics.com/2024-09-24T03:00:00Z/t_max_2m_24h:Ct_min_2m_24h:Crelative_humidity_2m:pwind_gusts_10m_1h:msprecip_24h:mmtotal_cloud_cover:octasmsl_pressure:hPa/polygon(-23.642215999,-46.674213,-23.6114339989999,-46.718221,-23.617119999,-46.74974,-23.594919999,-46.760663,-23.6090669989999,-46.807775,-23.5840099989999,-46.806459,-23.554834999,-46.760125,-23.520376999,-46.747045,-23.4941559989999,-46.758695,-23.5146879989999,-46.7264089999999,-23.5193029549999,-46.6252015009999,-23.5532970089999,-46.625203848,-23.5545829989999,-46.610221,-23.604665999,-46.579296,-23.645173999,-46.5845909999999,-23.675136999,-46.63358,-23.642215999,-46.674213)/json?model=mix
URL de requisição para a zona Zona Leste 1: https://api.meteomatics.com/2024-09-24T03:00:00Z/t_max_2m_24h:Ct_min_2m_24h:Crelative_humidity_2m:pwind_gusts_10m_1h:msprecip_24h:mmtotal_cloud_cover:octasmsl_pressure:hPa/polygon(-23.6008049989999,-46.575363,-23.5532970089999,-46.625

In [33]:
# Salvar os resultados em um arquivo CSV, por exemplo
for zona, df in dados_zonas.items():
    df.to_csv(f'dados_meteorologicos_{zona}.csv', index=False)

In [34]:
def adjust_value(value):
    if pd.notnull(value):
        return round(float(value), 2)
    return None

logging.info("Iniciando a inserção de dados.")

for zona_nome, df in dados_zonas.items():
    zona_id = int(Select_TBL_Zona.loc[Select_TBL_Zona['NM_ZONA'] == zona_nome, 'CD_ZONA'].values[0])
    df['CD_ZONA'] = zona_id

    # Converter 'DATA_FUTURA' para datetime se necessário
    if not pd.api.types.is_datetime64_any_dtype(df['DATA_FUTURA']):
        df['DATA_FUTURA'] = pd.to_datetime(df['DATA_FUTURA'])

    for i, row in df.iterrows():
        sql_insert = """
        INSERT INTO tb_clima_prev 
        (tb_zona_cd_zona, dt_referencia, dt_futura, temp_max, temp_min, umid_max, vel_vento, vol_precipitacao, tp_nuvem, pressao_atm)
        VALUES 
        (:CD_ZONA, :Data_Referencia, :Data_Futura, :Temperatura_Max, :Temperatura_Min, :Umidade_Max, :Ventania, :Precipitacao, :Nuvem, :Pressao)
        """
        data_insert = {
                'CD_ZONA': zona_id,
                'Data_Referencia': startdate,
                'Data_Futura': row['DATA_FUTURA'],
                'Temperatura_Max': adjust_value(row.get('TEMP_MAX')),
                'Temperatura_Min': adjust_value(row.get('TEMP_MIN')),
                'Umidade_Max': adjust_value(row.get('UMID_MAX')),
                'Ventania': adjust_value(row.get('VEL_VENTO')),
                'Precipitacao': adjust_value(row.get('VOL_PRECIPITACAO')),
                'Nuvem': row.get('TP_NUVEM'),
                'Pressao': adjust_value(row.get('PRESSAO_ATM'))
            }

        logging.info(f"Dados a serem inseridos para a linha {i+1} da zona {zona_nome}: {data_insert}")
        
        try:
            cursor.execute(sql_insert, data_insert)
            logging.info(f"Linha {i+1} inserida para a zona {zona_nome}.")
        except Exception as e:
            logging.error(f"Erro ao inserir a linha {i+1} para a zona {zona_nome}: {e}")
            continue
    
# Confirmar as alterações no banco de dados
connection.commit()
finaliza_conexao(cursor, connection)
logging.info("Inserção de dados concluída.")


2024-09-24 00:34:56,485 - INFO - Iniciando a inserção de dados.
2024-09-24 00:34:56,502 - INFO - Dados a serem inseridos para a linha 1 da zona Centro Ampliado: {'CD_ZONA': 1, 'Data_Referencia': datetime.datetime(2024, 9, 24, 3, 0), 'Data_Futura': Timestamp('2024-09-24 03:00:00+0000', tz='UTC'), 'Temperatura_Max': 32.2, 'Temperatura_Min': 15.1, 'Umidade_Max': 82.0, 'Ventania': 7.1, 'Precipitacao': 0.0, 'Nuvem': 0.0, 'Pressao': 1016.0}


2024-09-24 00:34:56,539 - INFO - Linha 1 inserida para a zona Centro Ampliado.
2024-09-24 00:34:56,542 - INFO - Dados a serem inseridos para a linha 2 da zona Centro Ampliado: {'CD_ZONA': 1, 'Data_Referencia': datetime.datetime(2024, 9, 24, 3, 0), 'Data_Futura': Timestamp('2024-09-24 04:00:00+0000', tz='UTC'), 'Temperatura_Max': 32.2, 'Temperatura_Min': 15.1, 'Umidade_Max': 85.1, 'Ventania': 7.1, 'Precipitacao': 0.0, 'Nuvem': 0.0, 'Pressao': 1015.7}
2024-09-24 00:34:56,561 - INFO - Linha 2 inserida para a zona Centro Ampliado.
2024-09-24 00:34:56,566 - INFO - Dados a serem inseridos para a linha 3 da zona Centro Ampliado: {'CD_ZONA': 1, 'Data_Referencia': datetime.datetime(2024, 9, 24, 3, 0), 'Data_Futura': Timestamp('2024-09-24 05:00:00+0000', tz='UTC'), 'Temperatura_Max': 32.2, 'Temperatura_Min': 15.1, 'Umidade_Max': 83.9, 'Ventania': 6.4, 'Precipitacao': 0.0, 'Nuvem': 0.0, 'Pressao': 1015.3}
2024-09-24 00:34:56,586 - INFO - Linha 3 inserida para a zona Centro Ampliado.
2024-09-24 00